In [2]:
import cv2
import numpy as np
import sys

#Read points from  text file
def readPoints(path):
    # Create an array of points
    points = []
    # Read points
    with open(path) as file:
        for line in file:
            index,x,y = line.split()
            points.append((int(x),int(y)))
    return points

def a(points,img):
    triangleList = 0
    size = img.shape
    print(size)
    rect = (0, 0, size[1], size[0])
    # 创建Subdiv2D 实例
    subdiv = cv2.Subdiv2D(rect)
    file_handle = open(r'C:\head\tri_age1.txt', mode='w')
    for p in points :
        subdiv.insert(p)
        triangleList = subdiv.getTriangleList();
        for t in triangleList :
            print("t:{}".format(t))
            pt1 = (t[0], t[1])
            print("=======")
            print("pt1:{}".format(pt1))
            pt2 = (t[2], t[3])
            print("pt2:{}".format(pt2))
            pt3 = (t[4], t[5])
            print("pt3:{}".format(pt3))
            print("=======")
            pt_int_1_1 = (int(t[0]),int(t[1]))
            pt_int_1_2 = (int(t[2]),int(t[3]))
            pt_int_1_3 = (int(t[4]),int(t[5]))
            i_num = 0
            for po in points:
                i_num += 1
                po_str=str(po)
                if str(pt_int_1_1) in po_str:
                    print(i_num)
                    print(pt_int_1_1)
                    file_handle.write(str(i_num)+' ')
                    

            i_num = 0
            for po in points:
                po_str=str(po)
                i_num += 1
                if str(pt_int_1_2) in po_str:
                    print(i_num)
                    print(pt_int_1_2)
                    file_handle.write(str(i_num)+' ')
                
            i_num = 0
            for po in points:
                po_str=str(po)
                i_num += 1
                if str(pt_int_1_3) in po_str:
                    print(i_num)
                    print(pt_int_1_3)
                    file_handle.write(str(i_num))
                    file_handle.write('\n') 
    file_handle.close()

        
# Apply affine tranform calculated using srcTri and sdtTri to src and output an image of size
def applyAffineTransform(src,srcTri,dstTri,size):


    warpMat = cv2.getAffineTransform(np.float32(srcTri),np.float32(dstTri))
    dst = cv2.warpAffine(src,warpMat,(size[0],size[1]),None,flags=cv2.INTER_LINEAR,borderMode=cv2.BORDER_REFLECT_101)

    return dst

# Warps and alpha blends triangular regions from img1 and img2 to img
def morphTriangle(img1,img2,img,t1,t2,t,alpha):

    #Find bounding rectangle for each triangle
    r1 = cv2.boundingRect(np.float32([t1]))
    r2 = cv2.boundingRect(np.float32([t2]))
    r = cv2.boundingRect(np.float32([t]))

    # Offset points by left top corner of the respective rectangles
    t1Rect = []
    t2Rect = []
    tRect = []

    for i in range(0,3):
        tRect.append(((t[i][0] - r[0]),(t[i][1]-r[1])))
        t1Rect.append(((t1[i][0]-r1[0]),(t1[i][1]-r1[1])))
        t2Rect.append(((t2[i][0] -r2[0]),(t2[i][1]-r2[1])))

    # Get mask by filling triangles
    mask = np.zeros((r[3],r[2],3),dtype = np.float32)
    cv2.fillConvexPoly(mask,np.int32(tRect),(1.0,1.0,1.0),16,0)

    # Apply warpImage to small rectangular patched
    img1Rect = img1[r1[1]:r1[1]+r1[3],r1[0]:r1[0]+r1[2]]
    img2Rect = img2[r2[1]:r2[1]+r2[3],r2[0]:r2[0]+r2[2]]

    size = (r[2],r[3])
    warpImage1 = applyAffineTransform(img1Rect,t1Rect,tRect,size)
    warpImage2 = applyAffineTransform(img2Rect,t2Rect,tRect,size)
    
    # Alpha blend rectangular patches
    imgRect = (1.0-alpha) *warpImage1 +alpha*warpImage2
#     imgRect = 0.1*warpImage1 + 0.9*warpImage2
    # Copy triangular region of rectangular patch to tje output image
    print(r[1],r[3],r[0],r[2])
    print(imgRect.shape)
    img[r[1]:r[1]+r[3],r[0]:r[0]+r[2]] = img[r[1]:r[1]+r[3],r[0]:r[0]+r[2]]*(1-mask) +imgRect*mask
    return img


if __name__ =='__main__':
    filename2 = 'C:\head\kage23.jpg'
    filename1 = 'C:\head\kage1.jpg'
   

    points_txt2 = 'C:\head\kage23.txt'
    points_txt1  = 'C:\head\kage1.txt'

#     alpha1 = 0.25
#     alpha2 = 0.50
#     alpha3 = 0.75
    
    alpha0 = 0.10
    alpha1 = 0.20
    alpha2 = 0.40
    alpha3 = 0.60
    alpha4 = 0.80
    alpha5 = 0.90

    # Read images
    img1 = cv2.imread(filename1)
    img2 = cv2.imread(filename2)

    # Convertat to float data type
    img1 = np.float32(img1)
    img2 = np.float32(img2)

    # Read array of corresponding points
    points1 = readPoints(points_txt1)
    points2 = readPoints(points_txt2)
    points = []
    points0_new = []
    points2_new = []
    points3_new = []
    points4_new = []
    points5_new = []

    a(points1,img1)
    # Compute weighted average point coordinate

    for i in range(0,len(points1)):
        
        x0 = (1-alpha0) *points1[i][0] +alpha0 *points2[i][0]
        y0 = (1-alpha0)*points1[i][1] + alpha0*points2[i][1]
        points0_new.append((x0,y0))
        
        x1 = (1-alpha1) *points1[i][0] +alpha1 *points2[i][0]
        y1 = (1-alpha1)*points1[i][1] + alpha1*points2[i][1]
        points.append((x1,y1))
        x2 = (1-alpha2) *points1[i][0] +alpha2 *points2[i][0]
        y2 = (1-alpha2)*points1[i][1] + alpha2*points2[i][1]
        points2_new.append((x2,y2))
        x3 = (1-alpha3) *points1[i][0] +alpha3 *points2[i][0]
        y3 = (1-alpha3)*points1[i][1] + alpha3*points2[i][1]
        points3_new.append((x3,y3))
        x4 = (1-alpha4) *points1[i][0] +alpha4 *points2[i][0]
        y4 = (1-alpha4)*points1[i][1] + alpha4*points2[i][1]
        points4_new.append((x4,y4))
        x5 = (1-alpha5) *points1[i][0] +alpha5 *points2[i][0]
        y5 = (1-alpha5)*points1[i][1] + alpha5*points2[i][1]
        points5_new.append((x5,y5))
        
        
    imgMorph0 = np.zeros(img1.shape,dtype = img1.dtype)
    imgMorph1 = np.zeros(img1.shape,dtype = img1.dtype)
    imgMorph2 = np.zeros(img1.shape,dtype = img1.dtype)
    imgMorph3 = np.zeros(img1.shape,dtype = img1.dtype)
    imgMorph4 = np.zeros(img1.shape,dtype = img1.dtype)
    
    imgMorph5 = np.zeros(img1.shape,dtype = img1.dtype)
#     imgMorph6 = np.zeros(img1.shape,dtype = img1.dtype)
#     imgMorph7 = np.zeros(img1.shape,dtype = img1.dtype)
        
    # Read triangles for tri.txt
    with open(r"C:\head\tri_age1.txt") as file:
        for line in file:
            x,y,z = line.split()

            x = int(x)
            y = int(y)
            z = int(z)
            x -= 1
            y -= 1
            z -= 1
            t1 = [points1[x],points1[y],points1[z]]
            t2 = [points2[x],points2[y],points2[z]]
            t = [points[x],points[y],points[z]]
            t2_new = [points2_new[x],points2_new[y],points2_new[z]]
            t3_new = [points3_new[x],points3_new[y],points3_new[z]]
            t4_new = [points4_new[x],points4_new[y],points4_new[z]]
            t0_new = [points0_new[x],points0_new[y],points0_new[z]]
            t5_new = [points5_new[x],points5_new[y],points5_new[z]]
            # Morph one triangle at a time
            imgMorph0 = morphTriangle(img1,img2,imgMorph0,t1,t2,t0_new,alpha0)
            imgMorph1 = morphTriangle(img1,img2,imgMorph1,t1,t2,t,alpha1)
            imgMorph2 = morphTriangle(img1,img2,imgMorph2,t1,t2,t2_new,alpha2)
            imgMorph3 = morphTriangle(img1,img2,imgMorph3,t1,t2,t3_new,alpha3)
            imgMorph4 = morphTriangle(img1,img2,imgMorph4,t1,t2,t4_new,alpha4)
            imgMorph5 = morphTriangle(img1,img2,imgMorph5,t1,t2,t5_new,alpha5)



    # Display Results
 
    out_img = np.hstack((img1,imgMorph0,imgMorph1,imgMorph2,imgMorph3,imgMorph4,imgMorph5,img2))
    cv2.imwrite("C:\head\out_imgktimgff.jpg",out_img)

    cv2.imshow("Morphed Face",np.uint8(imgMorph1))
    cv2.waitKey(0)



(1024, 1024, 3)
t:[123. 391. 161. 569. 130. 477.]
pt1:(123.0, 391.0)
pt2:(161.0, 569.0)
pt3:(130.0, 477.0)
3
(123, 391)
1
(161, 569)
2
(130, 477)
t:[161. 569. 123. 391. 122. 303.]
pt1:(161.0, 569.0)
pt2:(123.0, 391.0)
pt3:(122.0, 303.0)
1
(161, 569)
3
(123, 391)
4
(122, 303)
t:[123. 391. 161. 569. 130. 477.]
pt1:(123.0, 391.0)
pt2:(161.0, 569.0)
pt3:(130.0, 477.0)
3
(123, 391)
1
(161, 569)
2
(130, 477)
t:[161. 569. 123. 391. 148. 228.]
pt1:(161.0, 569.0)
pt2:(123.0, 391.0)
pt3:(148.0, 228.0)
1
(161, 569)
3
(123, 391)
5
(148, 228)
t:[123. 391. 161. 569. 130. 477.]
pt1:(123.0, 391.0)
pt2:(161.0, 569.0)
pt3:(130.0, 477.0)
3
(123, 391)
1
(161, 569)
2
(130, 477)
t:[148. 228. 123. 391. 122. 303.]
pt1:(148.0, 228.0)
pt2:(123.0, 391.0)
pt3:(122.0, 303.0)
5
(148, 228)
3
(123, 391)
4
(122, 303)
t:[161. 569. 123. 391. 203. 166.]
pt1:(161.0, 569.0)
pt2:(123.0, 391.0)
pt3:(203.0, 166.0)
1
(161, 569)
3
(123, 391)
6
(203, 166)
t:[123. 391. 161. 569. 130. 477.]
pt1:(123.0, 391.0)
pt2:(161.0, 569.0)
pt

pt1:(161.0, 569.0)
pt2:(736.0, 466.0)
pt3:(790.0, 531.0)
1
(161, 569)
16
(736, 466)
19
(790, 531)
t:[742. 401. 735. 337. 785. 434.]
pt1:(742.0, 401.0)
pt2:(735.0, 337.0)
pt3:(785.0, 434.0)
15
(742, 401)
14
(735, 337)
17
(785, 434)
t:[736. 466. 742. 401. 785. 434.]
pt1:(736.0, 466.0)
pt2:(742.0, 401.0)
pt3:(785.0, 434.0)
16
(736, 466)
15
(742, 401)
17
(785, 434)
t:[736. 466. 819. 465. 790. 531.]
pt1:(736.0, 466.0)
pt2:(819.0, 465.0)
pt3:(790.0, 531.0)
16
(736, 466)
18
(819, 465)
19
(790, 531)
t:[819. 465. 736. 466. 785. 434.]
pt1:(819.0, 465.0)
pt2:(736.0, 466.0)
pt3:(785.0, 434.0)
18
(819, 465)
16
(736, 466)
17
(785, 434)
t:[123. 391. 742. 401. 736. 466.]
pt1:(123.0, 391.0)
pt2:(742.0, 401.0)
pt3:(736.0, 466.0)
3
(123, 391)
15
(742, 401)
16
(736, 466)
t:[742. 401. 123. 391. 735. 337.]
pt1:(742.0, 401.0)
pt2:(123.0, 391.0)
pt3:(735.0, 337.0)
15
(742, 401)
3
(123, 391)
14
(735, 337)
t:[268. 119. 707. 250. 123. 391.]
pt1:(268.0, 119.0)
pt2:(707.0, 250.0)
pt3:(123.0, 391.0)
7
(268, 119)
13

t:[736. 466. 754. 591. 729. 638.]
pt1:(736.0, 466.0)
pt2:(754.0, 591.0)
pt3:(729.0, 638.0)
16
(736, 466)
20
(754, 591)
21
(729, 638)
t:[754. 591. 736. 466. 790. 531.]
pt1:(754.0, 591.0)
pt2:(736.0, 466.0)
pt3:(790.0, 531.0)
20
(754, 591)
16
(736, 466)
19
(790, 531)
t:[736. 466. 742. 401. 785. 434.]
pt1:(736.0, 466.0)
pt2:(742.0, 401.0)
pt3:(785.0, 434.0)
16
(736, 466)
15
(742, 401)
17
(785, 434)
t:[736. 466. 819. 465. 790. 531.]
pt1:(736.0, 466.0)
pt2:(819.0, 465.0)
pt3:(790.0, 531.0)
16
(736, 466)
18
(819, 465)
19
(790, 531)
t:[819. 465. 736. 466. 785. 434.]
pt1:(819.0, 465.0)
pt2:(736.0, 466.0)
pt3:(785.0, 434.0)
18
(819, 465)
16
(736, 466)
17
(785, 434)
t:[705. 723. 754. 591. 790. 531.]
pt1:(705.0, 723.0)
pt2:(754.0, 591.0)
pt3:(790.0, 531.0)
22
(705, 723)
20
(754, 591)
19
(790, 531)
t:[754. 591. 705. 723. 729. 638.]
pt1:(754.0, 591.0)
pt2:(705.0, 723.0)
pt3:(729.0, 638.0)
20
(754, 591)
22
(705, 723)
21
(729, 638)
t:[161. 569. 729. 638. 500. 878.]
pt1:(161.0, 569.0)
pt2:(729.0, 638.

10
(502, 72)
13
(707, 250)
t:[502.  72. 329.  90. 397.  69.]
pt1:(502.0, 72.0)
pt2:(329.0, 90.0)
pt3:(397.0, 69.0)
10
(502, 72)
8
(329, 90)
9
(397, 69)
t:[707. 250. 502.  72. 591. 106.]
pt1:(707.0, 250.0)
pt2:(502.0, 72.0)
pt3:(591.0, 106.0)
13
(707, 250)
10
(502, 72)
11
(591, 106)
t:[707. 250. 591. 106. 670. 163.]
pt1:(707.0, 250.0)
pt2:(591.0, 106.0)
pt3:(670.0, 163.0)
13
(707, 250)
11
(591, 106)
12
(670, 163)
t:[123. 391. 707. 250. 735. 337.]
pt1:(123.0, 391.0)
pt2:(707.0, 250.0)
pt3:(735.0, 337.0)
3
(123, 391)
13
(707, 250)
14
(735, 337)
t:[735. 337. 707. 250. 819. 465.]
pt1:(735.0, 337.0)
pt2:(707.0, 250.0)
pt3:(819.0, 465.0)
14
(735, 337)
13
(707, 250)
18
(819, 465)
t:[735. 337. 819. 465. 785. 434.]
pt1:(735.0, 337.0)
pt2:(819.0, 465.0)
pt3:(785.0, 434.0)
14
(735, 337)
18
(819, 465)
17
(785, 434)
t:[161. 569. 736. 466. 198. 678.]
pt1:(161.0, 569.0)
pt2:(736.0, 466.0)
pt3:(198.0, 678.0)
1
(161, 569)
16
(736, 466)
29
(198, 678)
t:[742. 401. 735. 337. 785. 434.]
pt1:(742.0, 401.0)
p

34
(169, 511)
7
(268, 119)
t:[169. 511. 329.  90. 707. 250.]
pt1:(169.0, 511.0)
pt2:(329.0, 90.0)
pt3:(707.0, 250.0)
34
(169, 511)
8
(329, 90)
13
(707, 250)
t:[ 95. 554. 169. 511. 161. 569.]
pt1:(95.0, 554.0)
pt2:(169.0, 511.0)
pt3:(161.0, 569.0)
33
(95, 554)
34
(169, 511)
1
(161, 569)
t:[169. 511.  95. 554. 130. 477.]
pt1:(169.0, 511.0)
pt2:(95.0, 554.0)
pt3:(130.0, 477.0)
34
(169, 511)
33
(95, 554)
2
(130, 477)
t:[130. 477.  95. 554. 123. 391.]
pt1:(130.0, 477.0)
pt2:(95.0, 554.0)
pt3:(123.0, 391.0)
2
(130, 477)
33
(95, 554)
3
(123, 391)
t:[122. 303. 203. 166. 123. 391.]
pt1:(122.0, 303.0)
pt2:(203.0, 166.0)
pt3:(123.0, 391.0)
4
(122, 303)
6
(203, 166)
3
(123, 391)
t:[203. 166. 122. 303. 148. 228.]
pt1:(203.0, 166.0)
pt2:(122.0, 303.0)
pt3:(148.0, 228.0)
6
(203, 166)
4
(122, 303)
5
(148, 228)
t:[130. 477. 123. 391. 169. 511.]
pt1:(130.0, 477.0)
pt2:(123.0, 391.0)
pt3:(169.0, 511.0)
2
(130, 477)
3
(123, 391)
34
(169, 511)
t:[123. 391.  95. 554. 122. 303.]
pt1:(123.0, 391.0)
pt2:(95.0,

...

571 54 419 81
(54, 81, 3)
570 58 351 70
(58, 70, 3)
560 61 354 70
(61, 70, 3)
540 67 359 71
(67, 71, 3)
521 72 364 72
(72, 72, 3)
501 78 369 73
(78, 73, 3)
491 81 372 73
(81, 73, 3)
577 88 351 70
(88, 70, 3)
567 93 354 70
(93, 70, 3)
547 103 359 71
(103, 71, 3)
527 113 364 72
(113, 72, 3)
507 123 369 73
(123, 73, 3)
497 128 372 73
(128, 73, 3)
577 88 328 76
(88, 76, 3)
567 93 330 76
(93, 76, 3)
547 103 335 75
(103, 75, 3)
527 113 340 74
(113, 74, 3)
507 123 345 73
(123, 73, 3)
497 128 347 73
(128, 73, 3)
579 161 239 165
(161, 165, 3)
569 172 243 163
(172, 163, 3)
549 194 251 159
(194, 159, 3)
528 216 258 156
(216, 156, 3)
508 238 266 152
(238, 152, 3)
498 249 270 150
(249, 150, 3)
579 86 302 102
(86, 102, 3)
569 91 305 101
(91, 101, 3)
549 101 310 100
(101, 100, 3)
528 112 316 98
(112, 98, 3)
508 122 321 97
(122, 97, 3)
498 127 324 96
(127, 96, 3)
561 19 283 20
(19, 20, 3)
550 20 286 20
(20, 20, 3)
528 22 291 20
(22, 20, 3)
506 23 295 22
(23, 22, 3)
484 25 299 23
(25, 23, 3)
473 26 301

606 37 429 51
(37, 51, 3)
592 44 435 54
(44, 54, 3)
578 51 441 57
(51, 57, 3)
571 54 444 59
(54, 59, 3)
604 25 420 46
(25, 46, 3)
598 26 423 48
(26, 48, 3)
586 28 429 51
(28, 51, 3)
574 29 435 54
(29, 54, 3)
562 31 441 57
(31, 57, 3)
556 32 444 59
(32, 59, 3)
506 59 104 72
(59, 72, 3)
502 59 114 68
(59, 68, 3)
493 59 134 60
(59, 60, 3)
484 60 153 53
(60, 53, 3)
475 60 173 45
(60, 45, 3)
470 61 183 42
(61, 42, 3)
472 77 104 72
(77, 72, 3)
468 76 114 68
(76, 68, 3)
459 75 134 60
(75, 60, 3)
451 72 153 53
(72, 53, 3)
442 71 171 47
(71, 47, 3)
438 70 176 48
(70, 48, 3)
472 77 0 136
(77, 136, 3)
468 76 0 141
(76, 141, 3)
459 75 0 151
(75, 151, 3)
451 72 0 162
(72, 162, 3)
442 71 0 174
(71, 174, 3)
438 74 0 184
(74, 184, 3)
299 82 128 141
(82, 141, 3)
295 83 135 143
(83, 143, 3)
287 84 149 147
(84, 147, 3)
279 85 163 151
(85, 151, 3)
271 86 177 155
(86, 155, 3)
267 87 184 157
(87, 157, 3)
299 87 128 91
(87, 91, 3)
295 86 133 92
(86, 92, 3)
287 84 143 93
(84, 93, 3)
279 85 153 94
(85, 94, 3)


725 299 655 369
(299, 369, 3)
728 296 661 363
(296, 363, 3)
733 291 673 351
(291, 351, 3)
739 285 686 338
(285, 338, 3)
744 280 698 326
(280, 326, 3)
747 277 704 320
(277, 320, 3)
801 223 592 432
(223, 432, 3)
802 222 597 427
(222, 427, 3)
805 219 607 417
(219, 417, 3)
808 216 617 407
(216, 407, 3)
811 213 627 397
(213, 397, 3)
812 212 632 392
(212, 392, 3)
641 85 528 206
(85, 206, 3)
641 88 535 204
(88, 204, 3)
632 102 549 200
(102, 200, 3)
624 116 563 195
(116, 195, 3)
615 130 577 191
(130, 191, 3)
611 137 584 189
(137, 189, 3)
511 513 709 315
(513, 315, 3)
511 513 714 310
(513, 310, 3)
511 513 724 300
(513, 300, 3)
511 513 733 291
(513, 291, 3)
511 513 743 281
(513, 281, 3)
511 513 748 276
(513, 276, 3)
542 29 362 27
(29, 27, 3)
531 30 366 27
(30, 27, 3)
509 32 374 26
(32, 26, 3)
487 35 382 25
(35, 25, 3)
465 37 390 24
(37, 24, 3)
454 38 394 24
(38, 24, 3)
542 36 351 24
(36, 24, 3)
531 37 354 24
(37, 24, 3)
509 39 359 25
(39, 25, 3)
487 41 364 26
(41, 26, 3)
465 43 369 27
(43, 27, 3

497 198 253 72
(198, 72, 3)
488 74 266 26
(74, 26, 3)
479 72 266 28
(72, 28, 3)
458 71 266 32
(71, 32, 3)
436 71 266 36
(71, 36, 3)
414 71 266 40
(71, 40, 3)
403 71 266 42
(71, 42, 3)
299 133 570 28
(133, 28, 3)
300 122 579 33
(122, 33, 3)
302 100 596 44
(100, 44, 3)
303 79 613 55
(79, 55, 3)
305 57 630 66
(57, 66, 3)
306 46 639 71
(46, 71, 3)
458 30 373 69
(30, 69, 3)
448 31 381 68
(31, 68, 3)
427 34 397 65
(34, 65, 3)
406 37 413 63
(37, 63, 3)
385 40 429 60
(40, 60, 3)
374 42 437 59
(42, 59, 3)
483 35 373 74
(35, 74, 3)
470 39 381 73
(39, 73, 3)
444 48 397 70
(48, 70, 3)
418 57 413 67
(57, 67, 3)
392 66 429 64
(66, 64, 3)
379 70 437 62
(70, 62, 3)
435 74 587 27
(74, 27, 3)
430 73 598 29
(73, 29, 3)
419 71 619 35
(71, 35, 3)
408 69 641 41
(69, 41, 3)
397 67 662 47
(67, 47, 3)
392 66 673 50
(66, 50, 3)
431 19 587 26
(19, 26, 3)
421 22 598 29
(22, 29, 3)
401 28 619 35
(28, 35, 3)
381 34 641 41
(34, 41, 3)
361 40 662 47
(40, 47, 3)
351 43 673 50
(43, 50, 3)
437 23 499 42
(23, 42, 3)
426 

784 114 496 25
(114, 25, 3)
778 127 502 27
(127, 27, 3)
775 133 505 28
(133, 28, 3)
759 34 417 22
(34, 22, 3)
756 34 417 24
(34, 24, 3)
750 34 417 28
(34, 28, 3)
745 34 417 31
(34, 31, 3)
739 34 417 35
(34, 35, 3)
736 34 417 37
(34, 37, 3)
681 65 454 36
(65, 36, 3)
679 64 458 37
(64, 37, 3)
674 63 465 40
(63, 40, 3)
669 63 473 41
(63, 41, 3)
664 64 480 44
(64, 44, 3)
661 65 484 45
(65, 45, 3)
751 47 438 36
(47, 36, 3)
750 46 440 38
(46, 38, 3)
747 45 444 42
(45, 42, 3)
744 44 447 47
(44, 47, 3)
739 45 451 51
(45, 51, 3)
736 46 453 53
(46, 53, 3)
745 15 438 36
(15, 36, 3)
742 15 440 38
(15, 38, 3)
736 15 444 42
(15, 42, 3)
730 16 447 47
(16, 47, 3)
724 18 451 51
(18, 51, 3)
721 19 453 53
(19, 53, 3)
741 11 454 36
(11, 36, 3)
739 12 458 37
(12, 37, 3)
735 13 465 40
(13, 40, 3)
730 15 473 41
(15, 41, 3)
724 18 480 44
(18, 44, 3)
721 19 484 45
(19, 45, 3)
749 51 473 40
(51, 40, 3)
748 49 477 43
(49, 43, 3)
745 46 485 49
(46, 49, 3)
743 42 493 54
(42, 54, 3)
740 39 501 60
(39, 60, 3)
739 37